# IP_VincentVonBueren_MachineLearning_4

This notebook is based on a data challenge from the Michigan Data Science Team ([MDST](http://midas.umich.edu/mdst/)). 

The Michigan Data Science Team ([MDST](http://midas.umich.edu/mdst/)) and the Michigan Student Symposium for Interdisciplinary Statistical Sciences ([MSSISS](https://sites.lsa.umich.edu/mssiss/)) have partnered with the City of Detroit to help solve one of the most pressing problems facing Detroit - blight. [Blight violations](http://www.detroitmi.gov/How-Do-I/Report/Blight-Complaint-FAQs) are issued by the city to individuals who allow their properties to remain in a deteriorated condition. Every year, the city of Detroit issues millions of dollars in fines to residents and every year, many of these fines remain unpaid. Enforcing unpaid blight fines is a costly and tedious process, so the city wants to know: how can we increase blight ticket compliance?

The first step in answering this question is understanding when and why a resident might fail to comply with a blight ticket. This is where predictive modeling comes in. Therefore, the main task is to predict whether a given blight ticket will be paid on time.

All data has been provided to through the [Detroit Open Data Portal](https://data.detroitmi.gov/). Nonetheless, it should be noted that it surely makes sense to look into data from other Detroit datasets to help inform feature creation and model selection. Here is a list of related datasets:

* [Building Permits](https://data.detroitmi.gov/Property-Parcels/Building-Permits/xw2a-a7tf)
* [Trades Permits](https://data.detroitmi.gov/Property-Parcels/Trades-Permits/635b-dsgv)
* [Improve Detroit: Submitted Issues](https://data.detroitmi.gov/Government/Improve-Detroit-Submitted-Issues/fwz3-w3yn)
* [DPD: Citizen Complaints](https://data.detroitmi.gov/Public-Safety/DPD-Citizen-Complaints-2016/kahe-efs3)
* [Parcel Map](https://data.detroitmi.gov/Property-Parcels/Parcel-Map/fxkw-udwf)

___

There are two data files in order to train and validate the models: train.csv and test.csv. Each row in these two files corresponds to a single blight ticket, and includes information about when, why, and to whom each ticket was issued. The target variable is compliance, which is True if the ticket was paid early, on time, or within one month of the hearing data, False if the ticket was paid after the hearing date or not at all, and Null if the violator was found not responsible. Compliance, as well as a handful of other variables that will not be available at test-time, are only included in train.csv.

__Note__: All tickets where the violators were found not responsible are not considered during evaluation. They are included in the training set as an additional source of data for visualization, and to enable unsupervised and semi-supervised approaches. However, they are not included in the test set.

<br>

**File descriptions** (Use only this data for training your model!)

    readonly/train.csv - the training set (all tickets issued 2004-2011)
    readonly/test.csv - the test set (all tickets issued 2012-2016)
    readonly/addresses.csv & readonly/latlons.csv - mapping from ticket id to addresses, and from addresses to lat/lon coordinates. 
     Note: misspelled addresses may be incorrectly geolocated.

<br>

**Data fields**

train.csv & test.csv

    ticket_id - unique identifier for tickets
    agency_name - Agency that issued the ticket
    inspector_name - Name of inspector that issued the ticket
    violator_name - Name of the person/organization that the ticket was issued to
    violation_street_number, violation_street_name, violation_zip_code - Address where the violation occurred
    mailing_address_str_number, mailing_address_str_name, city, state, zip_code, non_us_str_code, country - Mailing address of the violator
    ticket_issued_date - Date and time the ticket was issued
    hearing_date - Date and time the violator's hearing was scheduled
    violation_code, violation_description - Type of violation
    disposition - Judgment and judgement type
    fine_amount - Violation fine amount, excluding fees
    admin_fee - $20 fee assigned to responsible judgments
state_fee - $10 fee assigned to responsible judgments
    late_fee - 10% fee assigned to responsible judgments
    discount_amount - discount applied, if any
    clean_up_cost - DPW clean-up or graffiti removal cost
    judgment_amount - Sum of all fines and fees
    grafitti_status - Flag for graffiti violations
    
train.csv only

    payment_amount - Amount paid, if any
    payment_date - Date payment was made, if it was received
    payment_status - Current payment status as of Feb 1 2017
    balance_due - Fines and fees still owed
    collection_status - Flag for payments in collections
    compliance [target variable for prediction] 
     Null = Not responsible
     0 = Responsible, non-compliant
     1 = Responsible, compliant
    compliance_detail - More information on why each ticket was marked compliant or non-compliant


___

## Evaluation

Your predictions will be given as the probability that the corresponding blight ticket will be paid on time.

The evaluation metric for this assignment is the Area Under the ROC Curve (AUC). 

Your grade will be based on the AUC score computed for your classifier. A model which with an AUROC of 0.7 passes this assignment, over 0.75 will recieve full points.
___

For this assignment, create a function that trains a model to predict blight ticket compliance in Detroit using `readonly/train.csv`. Using this model, return a series of length 61001 with the data being the probability that each corresponding ticket from `readonly/test.csv` will be paid, and the index being the ticket_id.

Example:

    ticket_id
       284932    0.531842
       285362    0.401958
       285361    0.105928
       285338    0.018572
                 ...
       376499    0.208567
       376500    0.818759
       369851    0.018528
       Name: compliance, dtype: float32
       

In [1]:
import pandas as pd
import numpy as np
pd.set_option('display.max_columns', 500)

def blight_model():
    
    from sklearn.metrics import roc_curve, roc_auc_score
    from sklearn.model_selection import train_test_split, cross_val_score, GridSearchCV
    #from sklearn.svm import SVC
    #from sklearn.linear_model import LogisticRegression
    from sklearn.ensemble import GradientBoostingClassifier

    # First, I load the data
    
    train = pd.read_csv("other/train.csv", encoding = 'ISO-8859-1')
    test = pd.read_csv("other/test.csv")
    addresses = pd.read_csv("other/addresses.csv")
    latlons = pd.read_csv("other/latlons.csv")
    
    # Preprocessing of data
    
    # Merging the data frames 
    train = train.merge(addresses, on='ticket_id')
    train = train.merge(latlons, on='address')
    test = test.merge(addresses, on='ticket_id')
    test = test.merge(latlons, on='address')
   
    # Filters rows where country is not US and city is not Detroit
    train_clean = train[train.country.str.contains("USA", case=False)]
    test_clean = test[test.country.str.contains("USA", case=False) ]

    # Filters rows where complaince is not defined
    train_clean = train_clean[pd.notnull(train_clean.compliance)]

    # Drops columns which are not further needed
    train_clean.drop(['agency_name', 'inspector_name', 'violator_name', 'non_us_str_code', 'violation_description', 
                'grafitti_status', 'state_fee', 'admin_fee', 'ticket_issued_date', 'hearing_date', 'violation_code',
                      
                # columns that are not available in test set
                'payment_amount', 'balance_due', 'payment_date', 'payment_status', 
                'collection_status', 'compliance_detail', 
                      
                # columns which result from latlon
                'violation_zip_code', 'country', 'address', 'violation_street_number',
                'violation_street_name', 'mailing_address_str_number', 'mailing_address_str_name', 
                'city', 'state', 'zip_code', 'address'], axis=1, inplace=True)
    
    train_mask = list(train_clean.columns)
    train_mask.remove('compliance')
    test_clean = test_clean[train_mask]
    
    # Label Encoder 
    train_clean = pd.get_dummies(train_clean, prefix=['disposition'])
    test_clean = pd.get_dummies(test_clean, prefix=['disposition'])
    
    test_mask = list(test_clean.columns)
    #print(test_mask)
    test_mask.remove('disposition_Responsible by Dismissal')
    test_mask.remove('disposition_Responsible (Fine Waived) by Admis')
    test_mask.remove('disposition_Responsible - Compl/Adj by Default')
    test_mask.remove('disposition_Responsible - Compl/Adj by Determi')
    test_clean = test_clean[test_mask]
    #print(train_clean.columns)
    #print(train_clean.shape)
    #print(test_clean.columns)
    #print(test_clean.shape)
    
    # Fills the NaN values of the lat/lon entries
    train_clean['lat'] = train_clean['lat'].fillna(train_clean['lat'].mean())
    train_clean['lon'] = train_clean['lon'].fillna(train_clean['lon'].mean())
    test_clean['lat'] = test_clean['lat'].fillna(test_clean['lat'].mean())
    test_clean['lon'] = test_clean['lon'].fillna(test_clean['lon'].mean())

    
    # Data Seperation
    X_train, X_test, y_train, y_test = train_test_split(train_clean.iloc[:, train_clean.columns != 'compliance'], train_clean['compliance'], random_state=0)
    
    #print(y_train)
    
    #Scaling
    #from sklearn.preprocessing import MinMaxScaler
    #scaler = MinMaxScaler()
    #X_train_scaled = scaler.fit_transform(X_train)
    # we must apply the scaling to the test set that we computed for the training set
    #X_test_scaled = scaler.transform(X_test)
    #X_final_scaled = scaler.transform(test_clean)
    
    '''
    # Classifier 2 - LogReg
    lr = LogisticRegression()
    grid_values2 = {'C': [0.01, 0.1, 1, 10, 100], 'penalty': ['l1', 'l2']}
    grid_lr_auc = GridSearchCV(lr, param_grid = grid_values2, scoring='roc_auc')
    grid_lr_auc.fit(X_train, y_train)
    print('Grid best parameter (max. AUC): ', grid_lr_auc.best_params_)
    print('Grid best score (AUC): ', grid_lr_auc.best_score_)'''
    
    '''
    # Classifier 1 - SVC (rbf)
    svc_clf = SVC(kernel='rbf')
    grid_values1 = {'gamma': [0.1, 1, 10, 100]}
    grid_svc_clf_auc = GridSearchCV(svc_clf, param_grid = grid_values1, scoring = 'roc_auc')
    grid_svc_clf_auc.fit(X_train_scaled, y_train)
    print('Grid best parameter (max. AUC): ', grid_svc_clf_auc.best_params_)
    print('Grid best score (AUC): ', grid_svc_clf_auc.best_score_)
    '''
    
    # Classifier 3 - Gradient Boosted Decision Tree
    #grid_values3 = {'n_estimators': [1,10], 'max_depth': [None, 30]}
    dt_clf = GradientBoostingClassifier(n_estimators=200, learning_rate = 0.01, max_depth = 3, random_state = 0)
    # grid_gbdt_auc = GridSearchCV(dt_clf, param_grid=grid_values3, scoring='roc_auc')
    dt_clf.fit(X_train, y_train)
    y_decision_scores_auc = dt_clf.decision_function(X_test) 
    #print('Grid best parameter (max. AUC): ', grid_gbdt_auc.best_params_)
    #print('Grid best score (AUC): ', grid_gbdt_auc.best_score_)
    score = roc_auc_score(y_test, y_decision_scores_auc)
    

    return pd.DataFrame(dt_clf.predict(test_clean ),test_clean.ticket_id)

In [2]:
blight_model()

FileNotFoundError: [Errno 2] File b'train.csv' does not exist: b'train.csv'